<a href="https://colab.research.google.com/github/shirleyrutgers/DataVis/blob/main/database.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

Database
Business Application and LQ Private Industry

Step 1. Download file from online and save in colab

Data

Business applications
https://docs.google.com/spreadsheets/d/e/2PACX-1vRl9ztuLbIaUzAFe1YgGB7IRhZL4P5W3dL3XeSCna8RXFdJAfIya78QR2otbTWE4w/pub?gid=13513596&single=true&output=csv

Industry Location Quotient
https://docs.google.com/spreadsheets/d/e/2PACX-1vRxQsQ5FEDOhsbuD4U76nKN8Ky_dZX6AfLQMqtqdJHHlz3guHAKUBzYb_cBfzEkaw/pub?gid=1931554944&single=true&output=csv


# Set Up

In [281]:
#---------------------------SETUP----------------------------------
#get useful libraries
import time, os, sys, re #basics
import zipfile, json, datetime, string   #string for annotating points in scatter
import numpy as np #basic math
from statistics import * #stats

import matplotlib.pyplot as plt #import pylab as plt #apparently discouraged now:
 #https://stackoverflow.com/questions/11469336/what-is-the-difference-between-pylab-and-pyplot
 #https://www.tutorialspoint.com/matplotlib/matplotlib_pylab_module.htm

import pandas as pd
import pandas_datareader as pdr
from pandas_datareader import wb
from pandas.io.formats.style import Styler
#s4 = Styler(df4, uuid_len=0, cell_ids=False)

import urllib  #weird, guess need to have os and pandas imported for this to work  %TODO/LATER ditch it, its weird anyway, just use wget/curl

from google.colab import files

#import webbrowser

import seaborn as sns

from google.colab import data_table
data_table.enable_dataframe_formatter() #this enables spreadsheet view upon calling dataframe (without() )

#tricks how to extend notebook functionality
#https://coderzcolumn.com/tutorials/python/list-of-useful-magic-commands-in-jupyter-notebook-lab
#will display all output not just last command
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "all"

###magics: https://ipython.readthedocs.io/en/stable/interactive/magics.html
#most essential setup for vis: it does affect vis! careful!! stick with inline, maybe notebook; others mostly for non-notebook, eg spyder environ
#https://jakevdp.github.io/PythonDataScienceHandbook/04.00-introduction-to-matplotlib.html recomends *inline*!
#show current one:
#%matplotlib
#%matplotlib --list
#interactive plots:
#%matplotlib notebook
#static images of your plot:
%matplotlib inline
#this one and other magics (btw default is probably agg)
#%matplotlib nbagg
##https://www.marktechpost.com/2023/10/20/6-magic-commands-for-jupyter-notebooks-in-python-data-science/
#%%latex
#%ai
#%run
#%writefile
#%history -n

###themes/styles: https://matplotlib.org/stable/gallery/style_sheets/style_sheets_reference.html
#https://jakevdp.github.io/PythonDataScienceHandbook/04.11-settings-and-stylesheets.html
#https://matplotlib.org/stable/tutorials/introductory/customizing.html
#here more about art and style than under the hood functionality as with magics, explore and experiment
#many may find 'default' or seaborn ones more pleasing; my fav 'classic' is back from 90s ;)
#plt.style.available #list available styles :) may install more
plt.style.use('default') # more delicate subtle than classic
#plt.style.use('classic')  #  'seaborn-whitegrid' 'seaborn-white' 'seaborn-poster'
# btw: magics v theme/style sequence matters, eg if i specify classic style before inline magic, i wouldnt get grey bounding box im getting

#sometimes have to install library which you get from https://pypi.org/
#!pip install geopandas

#Database 1. Business Application

In [282]:
# Read Database 1, Business Application, from URL CSV, from row 3
business = pd.read_csv(
    'https://docs.google.com/spreadsheets/d/e/2PACX-1vRl9ztuLbIaUzAFe1YgGB7IRhZL4P5W3dL3XeSCna8RXFdJAfIya78QR2otbTWE4w/pub?gid=13513596&single=true&output=csv',
    skiprows=2
)

# Review
business.head()

State          County  County Code  fipstate  fipscty BA2005 BA2006 BA2007  \
0    AL  Autauga County         1001         1        1    335    348    348   
1    AL  Baldwin County         1003         1        3   1986   2101   1975   
2    AL  Barbour County         1005         1        5    138    179    156   
3    AL     Bibb County         1007         1        7    118    145    117   
4    AL   Blount County         1009         1        9    315    323    297   

  BA2008 BA2009  ... BA2014 BA2015 BA2016 BA2017 BA2018 BA2019 BA2020 BA2021  \
0    367    288  ...    290    291    294    313    384    394    559    776   
1   1721   1505  ...   1575   1735   1858   2114   2104   2317   2697   3407   
2    139    133  ...    120    129    122    114    113    135    230    334   
3     98     98  ...    101     78     86     79    105     86    165    199   
4    306    247  ...    228    218    254    281    299    312    344    473   

  BA2022 BA2023  
0    707    703  
1   3694   3855  
2    266    421  
3    158    173  
4    428    513  

[5 rows x 24 columns]

In [283]:
# Delete unnecessary columns from business
cols_to_drop = [
    'fipstate', 'fipscty',        # IDs duplicados
    'BA2005', 'BA2006', 'BA2007', 'BA2008', 'BA2009',
    'BA2010', 'BA2011', 'BA2012', 'BA2013', 'BA2014',
    'BA2015', 'BA2016', 'BA2017', 'BA2018', 'BA2019',
    'BA2020', 'BA2021', 'BA2022'  # All years before 2023
]

# Apply the drop
business = business.drop(columns=cols_to_drop)

# Review the result
business.head()

State          County  County Code BA2023
0    AL  Autauga County         1001    703
1    AL  Baldwin County         1003   3855
2    AL  Barbour County         1005    421
3    AL     Bibb County         1007    173
4    AL   Blount County         1009    513

In [284]:
#Review the data type
print(business.dtypes)

State          object
County         object
County Code     int64
BA2023         object
dtype: object


In [285]:
# Convert BA2023 into numeric
business['BA2023'] = pd.to_numeric(business['BA2023'], errors='coerce')
print(business.dtypes)

State           object
County          object
County Code      int64
BA2023         float64
dtype: object


In [286]:
# First: make County Code a string
business['County Code'] = business['County Code'].astype(str)

# Second: Fill County Code with zeros to ensure 5 digits
business['County Code'] = business['County Code'].str.zfill(5)

In [287]:
# Replace NaN values in BA2023 with 0
business['BA2023'] = business['BA2023'].fillna(0)

In [288]:
# Count how many NaN are in BA2023
#Here, before I had 12 NaN, where BA2023 was empty, value=0
na_count = business['BA2023'].isna().sum()

print(f"Number of NaN in BA2023: {na_count}")


Number of NaN in BA2023: 0


In [289]:
# Show rows where BA2023 could not be converted (NaN)
business_nan_rows = business[business['BA2023'].isna()]

# Display them
business_nan_rows


Empty DataFrame
Columns: [State, County, County Code, BA2023]
Index: []

In [290]:
#Before merge, review the data type again
print(business.dtypes)

State           object
County          object
County Code     object
BA2023         float64
dtype: object


# Database 2. Industry

In [291]:
#Read Database 2> Industry Data from URL CSV
industry=pd.read_csv('https://docs.google.com/spreadsheets/d/e/2PACX-1vRxQsQ5FEDOhsbuD4U76nKN8Ky_dZX6AfLQMqtqdJHHlz3guHAKUBzYb_cBfzEkaw/pub?gid=1931554944&single=true&output=csv')
# Review
industry.head()

<ipython-input-291-bf5e9b1227ce>:2: DtypeWarning: Columns (1) have mixed types. Specify dtype option on import or set low_memory=False.
  industry=pd.read_csv('https://docs.google.com/spreadsheets/d/e/2PACX-1vRxQsQ5FEDOhsbuD4U76nKN8Ky_dZX6AfLQMqtqdJHHlz3guHAKUBzYb_cBfzEkaw/pub?gid=1931554944&single=true&output=csv')


Area\nCode  St  Cnty  Own  NAICS  Year Qtr Area Type St Name        Area  \
0      US000  US   0.0    0     10  2023   A    Nation     NaN  U.S. TOTAL   
1      US000  US   0.0    1     10  2023   A    Nation     NaN  U.S. TOTAL   
2      US000  US   0.0    2     10  2023   A    Nation     NaN  U.S. TOTAL   
3      US000  US   0.0    3     10  2023   A    Nation     NaN  U.S. TOTAL   
4      US000  US   0.0    5     10  2023   A    Nation     NaN  U.S. TOTAL   

            Ownership                  Industry Annual Average Status Code  \
0       Total Covered  10 Total, all industries                        NaN   
1  Federal Government  10 Total, all industries                        NaN   
2    State Government  10 Total, all industries                        NaN   
3    Local Government  10 Total, all industries                        NaN   
4             Private  10 Total, all industries                        NaN   

  Annual Average Establishment Count Annual Average Employment  \
0                         11,866,306               153,140,899   
1                             61,310                 2,929,938   
2                             72,215                 4,658,153   
3                            171,844                14,263,127   
4                         11,560,938               131,289,681   

   Annual Total Wages Annual Average Weekly Wage Annual Average Pay  \
0  11,081,267,615,470                      1,392             72,360   
1     286,764,744,238                      1,882             97,874   
2     356,315,881,354                      1,471             76,493   
3     905,493,894,970                      1,221             63,485   
4   9,532,693,094,908                      1,396             72,608   

   Employment Location Quotient Relative to U.S.  \
0                                            1.0   
1                                            1.0   
2                                            1.0   
3                                            1.0   
4                                            1.0   

   Total Wage Location Quotient Relative to U.S.  
0                                            1.0  
1                                            1.0  
2                                            1.0  
3                                            1.0  
4                                            1.0

In [292]:
#Cleanning the database> industry
#Rename the column Area
industry = industry.rename(columns={"Area": "County"})
#Rename the column Area Code
industry = industry.rename(columns={'Area\nCode': 'County Code'})

In [293]:
# Filter> County, industry Private Ownership, and Total Industry, delete "Unknow Or Undefined"
priv= industry[
    (industry["Area Type"] == "County") &
    (industry["Ownership"] == "Private") &
    (industry["Industry"] == "10 Total, all industries") &
    (~industry["County"].str.contains("Unknown", na=False))
]

# Display the filtered results
priv.head()

County Code  St  Cnty  Own  NAICS  Year Qtr Area Type  St Name  \
40        01001  01   1.0    5     10  2023   A    County  Alabama   
57        01003  01   3.0    5     10  2023   A    County  Alabama   
75        01005  01   5.0    5     10  2023   A    County  Alabama   
92        01007  01   7.0    5     10  2023   A    County  Alabama   
109       01009  01   9.0    5     10  2023   A    County  Alabama   

                      County Ownership                  Industry  \
40   Autauga County, Alabama   Private  10 Total, all industries   
57   Baldwin County, Alabama   Private  10 Total, all industries   
75   Barbour County, Alabama   Private  10 Total, all industries   
92      Bibb County, Alabama   Private  10 Total, all industries   
109   Blount County, Alabama   Private  10 Total, all industries   

    Annual Average Status Code Annual Average Establishment Count  \
40                         NaN                              1,011   
57                         NaN                              8,137   
75                         NaN                                533   
92                         NaN                                380   
109                        NaN                                867   

    Annual Average Employment Annual Total Wages Annual Average Weekly Wage  \
40                      9,330        454,329,752                        936   
57                     71,867      3,473,350,164                        929   
75                      6,227        264,209,398                        816   
92                      3,529        187,928,363                      1,024   
109                     6,734        293,597,353                        839   

    Annual Average Pay  Employment Location Quotient Relative to U.S.  \
40              48,696                                           0.92   
57              48,330                                           1.01   
75              42,433                                           0.94   
92              53,248                                           0.85   
109             43,602                                           0.89   

     Total Wage Location Quotient Relative to U.S.  
40                                            0.89  
57                                            1.00  
75                                            0.91  
92                                            0.88  
109                                           0.88

In [294]:
# Drop specific columns
cols_to_drop = ['St', 'Cnty', 'Own', 'NAICS', 'Year', 'Qtr', 'Annual Average Status Code']
priv = priv.drop(columns=cols_to_drop)

In [295]:
#Before merge, review the data type, here I just want to CHECK the COLUMN COUNTY CODE, after merge I will see what actions to do with these objetcs datatype
print(priv.dtypes)

County Code                                       object
Area Type                                         object
St Name                                           object
County                                            object
Ownership                                         object
Industry                                          object
Annual Average Establishment Count                object
Annual Average Employment                         object
Annual Total Wages                                object
Annual Average Weekly Wage                        object
Annual Average Pay                                object
Employment Location Quotient Relative to U.S.    float64
Total Wage Location Quotient Relative to U.S.    float64
dtype: object


# Merge

In [296]:
#Before Merge> Just check if County Code have same dtypes=object
print(business.dtypes)
print(priv.dtypes)

State           object
County          object
County Code     object
BA2023         float64
dtype: object
County Code                                       object
Area Type                                         object
St Name                                           object
County                                            object
Ownership                                         object
Industry                                          object
Annual Average Establishment Count                object
Annual Average Employment                         object
Annual Total Wages                                object
Annual Average Weekly Wage                        object
Annual Average Pay                                object
Employment Location Quotient Relative to U.S.    float64
Total Wage Location Quotient Relative to U.S.    float64
dtype: object


In [297]:
#TEST
# New business dataset: only County Code and BA2023
business_filtered = business[['County Code', 'BA2023']]

# New priv dataset: only County Code and Employment Location Quotient Relative to U.S.
priv_filtered = priv[['County Code', 'Employment Location Quotient Relative to U.S.']]

# Review the first few rows
business_filtered.head()
priv_filtered.head()


County Code  BA2023
0       01001   703.0
1       01003  3855.0
2       01005   421.0
3       01007   173.0
4       01009   513.0

County Code  Employment Location Quotient Relative to U.S.
40        01001                                           0.92
57        01003                                           1.01
75        01005                                           0.94
92        01007                                           0.85
109       01009                                           0.89

In [298]:
# Merge business and priv where County Code matches
#outer=keep all
merged = pd.merge(business, priv, how='outer', on='County Code', indicator=True)
# Review the first rows
merged

State           County_x County Code  BA2023 Area Type  St Name  \
0       AL     Autauga County       01001   703.0    County  Alabama   
1       AL     Baldwin County       01003  3855.0    County  Alabama   
2       AL     Barbour County       01005   421.0    County  Alabama   
3       AL        Bibb County       01007   173.0    County  Alabama   
4       AL      Blount County       01009   513.0    County  Alabama   
...    ...                ...         ...     ...       ...      ...   
3151    WY  Sweetwater County       56037   839.0    County  Wyoming   
3152    WY       Teton County       56039  1374.0    County  Wyoming   
3153    WY       Uinta County       56041   290.0    County  Wyoming   
3154    WY    Washakie County       56043   112.0    County  Wyoming   
3155    WY      Weston County       56045    74.0    County  Wyoming   

                        County_y Ownership                  Industry  \
0        Autauga County, Alabama   Private  10 Total, all industries   
1        Baldwin County, Alabama   Private  10 Total, all industries   
2        Barbour County, Alabama   Private  10 Total, all industries   
3           Bibb County, Alabama   Private  10 Total, all industries   
4         Blount County, Alabama   Private  10 Total, all industries   
...                          ...       ...                       ...   
3151  Sweetwater County, Wyoming   Private  10 Total, all industries   
3152       Teton County, Wyoming   Private  10 Total, all industries   
3153       Uinta County, Wyoming   Private  10 Total, all industries   
3154    Washakie County, Wyoming   Private  10 Total, all industries   
3155      Weston County, Wyoming   Private  10 Total, all industries   

     Annual Average Establishment Count Annual Average Employment  \
0                                 1,011                     9,330   
1                                 8,137                    71,867   
2                                   533                     6,227   
3                                   380                     3,529   
4                                   867                     6,734   
...                                 ...                       ...   
3151                              1,588                    16,760   
3152                              2,916                    20,680   
3153                                803                     6,115   
3154                                404                     2,818   
3155                                244                     1,605   

     Annual Total Wages Annual Average Weekly Wage Annual Average Pay  \
0           454,329,752                        936             48,696   
1         3,473,350,164                        929             48,330   
2           264,209,398                        816             42,433   
3           187,928,363                      1,024             53,248   
4           293,597,353                        839             43,602   
...                 ...                        ...                ...   
3151      1,178,570,755                      1,352             70,321   
3152      1,590,595,650                      1,479             76,914   
3153        304,737,470                        958             49,836   
3154        136,283,514                        930             48,356   
3155         80,726,466                        967             50,310   

      Employment Location Quotient Relative to U.S.  \
0                                              0.92   
1                                              1.01   
2                                              0.94   
3                                              0.85   
4                                              0.89   
...                                             ...   
3151                                           0.94   
3152                                           1.03   
3153                                           0.87   
3154               

In [299]:
#Results of merge
#Summary of merge results
merge_summary = merged['_merge'].value_counts()

print(merge_summary)


_merge
both          3142
left_only       14
right_only       0
Name: count, dtype: int64


In [300]:
# Count unique County Codes
unique_county_codes = merged['County Code'].nunique()

print(f"Unique County Codes: {unique_county_codes}")


Unique County Codes: 3156


In [301]:
# Total rows after merge
total_rows = merged.shape[0]

print(f"Total Rows in merged: {total_rows}")

Total Rows in merged: 3156


In [302]:
# Summary of match status
print(merged['_merge'].value_counts())

# How many unique County Codes
print(f"Unique County Codes: {merged['County Code'].nunique()}")

# Total rows
print(f"Total Rows: {merged.shape[0]}")


_merge
both          3142
left_only       14
right_only       0
Name: count, dtype: int64
Unique County Codes: 3156
Total Rows: 3156


In [303]:
# Filter for left_only (only in business, no match in priv)
left_only = merged[merged['_merge'] == 'left_only']

# Filter for right_only (only in priv, no match in business)
right_only = merged[merged['_merge'] == 'right_only']

# Display as nice tables
from IPython.display import display

print("Left Only (business but no priv):")
display(left_only)

print("\nRight Only (priv but no business):")
display(right_only)


Left Only (business but no priv):


State                                        County_x County Code  \
94      AK                      Valdez-Cordova Census Area       02261   
95      AK                        Wade Hampton Census Area       02270   
319     CT                         Capitol Planning Region       09110   
320     CT              Greater Bridgeport Planning Region       09120   
321     CT  Lower Connecticut River Valley Planning Region       09130   
322     CT                Naugatuck Valley Planning Region       09140   
323     CT        Northeastern Connecticut Planning Region       09150   
324     CT                 Northwest Hills Planning Region       09160   
325     CT       South Central Connecticut Planning Region       09170   
326     CT        Southeastern Connecticut Planning Region       09180   
327     CT             Western Connecticut Planning Region       09190   
560     HI                                  Kalawao County       15005   
2430    SD                                  Shannon County       46113   
2929    VA                                    Bedford city       51515   

       BA2023 Area Type St Name County_y Ownership Industry  \
94        0.0       NaN     NaN      NaN       NaN      NaN   
95        0.0       NaN     NaN      NaN       NaN      NaN   
319   11967.0       NaN     NaN      NaN       NaN      NaN   
320    5064.0       NaN     NaN      NaN       NaN      NaN   
321    1858.0       NaN     NaN      NaN       NaN      NaN   
322    5451.0       NaN     NaN      NaN       NaN      NaN   
323     819.0       NaN     NaN      NaN       NaN      NaN   
324    1188.0       NaN     NaN      NaN       NaN      NaN   
325    7390.0       NaN     NaN      NaN       NaN      NaN   
326    2577.0       NaN     NaN      NaN       NaN      NaN   
327   11644.0       NaN     NaN      NaN       NaN      NaN   
560       6.0       NaN     NaN      NaN       NaN      NaN   
2430      0.0       NaN     NaN      NaN       NaN      NaN   
2929      0.0       NaN     NaN      NaN       NaN      NaN   

     Annual Average Establishment Count Annual Average Employment  \
94                                  NaN                       NaN   
95                                  NaN                       NaN   
319                                 NaN                       NaN   
320                                 NaN                       NaN   
321                                 NaN                       NaN   
322                                 NaN                       NaN   
323                                 NaN                       NaN   
324                                 NaN                       NaN   
325                                 NaN                       NaN   
326                                 NaN                       NaN   
327                                 NaN                       NaN   
560                                 NaN                       NaN   
2430                                NaN                       NaN   
2929                                NaN                       NaN   

     Annual Total Wages Annual Average Weekly Wage Annual Average Pay  \
94                  NaN                        NaN                NaN   
95                  NaN                        NaN                NaN   
319                 NaN                        NaN                NaN   
320                 NaN                        NaN                NaN   
321                 NaN                        NaN                NaN   
322                 NaN                        NaN                NaN   
323                 NaN                        NaN                NaN   
324                 NaN                        NaN                NaN   
325                 NaN                        NaN                NaN   
326                 NaN                        NaN                NaN   
327                 NaN                        NaN                NaN   
560                 NaN             


Right Only (priv but no business):


Empty DataFrame
Columns: [State, County_x, County Code, BA2023, Area Type, St Name, County_y, Ownership, Industry, Annual Average Establishment Count, Annual Average Employment, Annual Total Wages, Annual Average Weekly Wage, Annual Average Pay, Employment Location Quotient Relative to U.S., Total Wage Location Quotient Relative to U.S., _merge]
Index: []

Counties/Regions present in business dataset but missing from priv (industry) dataset:

1. Valdez-Cordova Census Area, Alaska (AK)  
2. Wade Hampton Census Area, Alaska (AK)  
3. Capitol Planning Region, Connecticut (CT)  
4. Greater Bridgeport Planning Region, Connecticut (CT)  
5. Lower Connecticut River Valley Planning Region, Connecticut (CT)  
6. Naugatuck Valley Planning Region, Connecticut (CT)  
7. Northeastern Connecticut Planning Region, Connecticut (CT)  
8. Northwest Hills Planning Region, Connecticut (CT)  
9. South Central Connecticut Planning Region, Connecticut (CT)  
10. Southeastern Connecticut Planning Region, Connecticut (CT)  
11. Western Connecticut Planning Region, Connecticut (CT)  
12. Kalawao County, Hawaii (HI)  
13. Shannon County, South Dakota (SD)  
14. Bedford city, Virginia (VA)

#Final dataset merged

In [304]:
# Keep only rows where match happened in both datasets
businesspriv = merged[merged['_merge'] == 'both']

# Do not drop the _merge column, just drop these left_only (only in business, no match in priv)
# Just review the first rows
businesspriv.head()


State        County_x County Code  BA2023 Area Type  St Name  \
0    AL  Autauga County       01001   703.0    County  Alabama   
1    AL  Baldwin County       01003  3855.0    County  Alabama   
2    AL  Barbour County       01005   421.0    County  Alabama   
3    AL     Bibb County       01007   173.0    County  Alabama   
4    AL   Blount County       01009   513.0    County  Alabama   

                  County_y Ownership                  Industry  \
0  Autauga County, Alabama   Private  10 Total, all industries   
1  Baldwin County, Alabama   Private  10 Total, all industries   
2  Barbour County, Alabama   Private  10 Total, all industries   
3     Bibb County, Alabama   Private  10 Total, all industries   
4   Blount County, Alabama   Private  10 Total, all industries   

  Annual Average Establishment Count Annual Average Employment  \
0                              1,011                     9,330   
1                              8,137                    71,867   
2                                533                     6,227   
3                                380                     3,529   
4                                867                     6,734   

  Annual Total Wages Annual Average Weekly Wage Annual Average Pay  \
0        454,329,752                        936             48,696   
1      3,473,350,164                        929             48,330   
2        264,209,398                        816             42,433   
3        187,928,363                      1,024             53,248   
4        293,597,353                        839             43,602   

   Employment Location Quotient Relative to U.S.  \
0                                           0.92   
1                                           1.01   
2                                           0.94   
3                                           0.85   
4                                           0.89   

   Total Wage Location Quotient Relative to U.S. _merge  
0                                           0.89   both  
1                                           1.00   both  
2                                           0.91   both  
3                                           0.88   both  
4                                           0.88   both

In [305]:
# Total number of County Codes (unique)
total_county_codes = businesspriv['County Code'].nunique()

# Total sum of BA2023
total_ba2023 = pd.to_numeric(businesspriv['BA2023'], errors='coerce').sum()

# Average of BA2023
average_ba2023 = pd.to_numeric(businesspriv['BA2023'], errors='coerce').mean()

# Show results
print(f"Total unique County Codes: {total_county_codes}")
print(f"Total sum of BA2023: {total_ba2023}")
print(f"Average BA2023: {average_ba2023}")


Total unique County Codes: 3142
Total sum of BA2023: 5402970.0
Average BA2023: 1719.595798854233


In [306]:
# Columns you want to check for NaN
columns_to_check = [
    'Annual Average Establishment Count',
    'Annual Average Employment',
    'Annual Total Wages',
    'Annual Average Weekly Wage',
    'Annual Average Pay',
    'Employment Location Quotient Relative to U.S.',
    'Total Wage Location Quotient Relative to U.S.'
]

# Count NaN in each selected column
nan_counts = businesspriv[columns_to_check].isna().sum()

# Show result
print(nan_counts)


Annual Average Establishment Count               0
Annual Average Employment                        0
Annual Total Wages                               0
Annual Average Weekly Wage                       0
Annual Average Pay                               0
Employment Location Quotient Relative to U.S.    0
Total Wage Location Quotient Relative to U.S.    0
dtype: int64


#Download my database

Conclusion> my database is "businesspriv"

In [307]:
businesspriv.head()

State        County_x County Code  BA2023 Area Type  St Name  \
0    AL  Autauga County       01001   703.0    County  Alabama   
1    AL  Baldwin County       01003  3855.0    County  Alabama   
2    AL  Barbour County       01005   421.0    County  Alabama   
3    AL     Bibb County       01007   173.0    County  Alabama   
4    AL   Blount County       01009   513.0    County  Alabama   

                  County_y Ownership                  Industry  \
0  Autauga County, Alabama   Private  10 Total, all industries   
1  Baldwin County, Alabama   Private  10 Total, all industries   
2  Barbour County, Alabama   Private  10 Total, all industries   
3     Bibb County, Alabama   Private  10 Total, all industries   
4   Blount County, Alabama   Private  10 Total, all industries   

  Annual Average Establishment Count Annual Average Employment  \
0                              1,011                     9,330   
1                              8,137                    71,867   
2                                533                     6,227   
3                                380                     3,529   
4                                867                     6,734   

  Annual Total Wages Annual Average Weekly Wage Annual Average Pay  \
0        454,329,752                        936             48,696   
1      3,473,350,164                        929             48,330   
2        264,209,398                        816             42,433   
3        187,928,363                      1,024             53,248   
4        293,597,353                        839             43,602   

   Employment Location Quotient Relative to U.S.  \
0                                           0.92   
1                                           1.01   
2                                           0.94   
3                                           0.85   
4                                           0.89   

   Total Wage Location Quotient Relative to U.S. _merge  
0                                           0.89   both  
1                                           1.00   both  
2                                           0.91   both  
3                                           0.88   both  
4                                           0.88   both

In [308]:
# A1. Save the file as Excel inside Colab environment
businesspriv.to_excel('businesspriv.xlsx', index=False)

# 2. Download the file to your computer
from google.colab import files
files.download('businesspriv.xlsx')

# B1. Save the file as CSV inside Colab environment
#businesspriv.to_csv('businesspriv.csv', index=False)

# 2. Download the CSV file to your computer
#from google.colab import files
#files.download('businesspriv.csv')


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

# Issues

In [312]:
#BUT HERE WE HAVE A PROBLEM
#Annual Average Establishment Count	object
#Annual Average Employment	object
#Annual Total Wages	object
#Annual Average Weekly Wage	object
#Annual Average Pay	object
businesspriv.dtypes

State                                              object
County_x                                           object
County Code                                        object
BA2023                                            float64
Area Type                                          object
St Name                                            object
County_y                                           object
Ownership                                          object
Industry                                           object
Annual Average Establishment Count                 object
Annual Average Employment                          object
Annual Total Wages                                 object
Annual Average Weekly Wage                         object
Annual Average Pay                                 object
Employment Location Quotient Relative to U.S.     float64
Total Wage Location Quotient Relative to U.S.     float64
_merge                                           category
dtype: object

In [313]:
# Columns to sum, including BA2023
columns_to_sum = [
    'BA2023',
    'Annual Average Establishment Count',
    'Annual Average Employment',
    'Annual Total Wages',
    'Annual Average Weekly Wage',
    'Annual Average Pay',
    'Employment Location Quotient Relative to U.S.',
    'Total Wage Location Quotient Relative to U.S.'
]

# Sum each column
sums = businesspriv[columns_to_sum].apply(pd.to_numeric, errors='coerce').sum()

# Display result
print(sums)


BA2023                                           5402970.00
Annual Average Establishment Count                787588.00
Annual Average Employment                         194470.00
Annual Total Wages                                     0.00
Annual Average Weekly Wage                       1687166.00
Annual Average Pay                                     0.00
Employment Location Quotient Relative to U.S.       2833.84
Total Wage Location Quotient Relative to U.S.       2811.42
dtype: float64


In [314]:
# Columns to work with
columns = [
    'BA2023',
    'Annual Average Establishment Count',
    'Annual Average Employment',
    'Annual Total Wages',
    'Annual Average Weekly Wage',
    'Annual Average Pay',
    'Employment Location Quotient Relative to U.S.',
    'Total Wage Location Quotient Relative to U.S.'
]

# Calculate sum and count of non-null values for each column (HAVE TO BE 3142 EACH SUM OF COLUMN)
summary = {}

for col in columns:
    total_sum = pd.to_numeric(businesspriv[col], errors='coerce').sum()
    count = pd.to_numeric(businesspriv[col], errors='coerce').count()
    summary[col] = {'Sum': total_sum, 'Count of Non-NaN': count}

# Convert to a readable DataFrame
import pandas as pd
summary_df = pd.DataFrame(summary).T

# Show result
summary_df


Sum  Count of Non-NaN
BA2023                                         5402970.00            3142.0
Annual Average Establishment Count              787588.00            1982.0
Annual Average Employment                       194470.00             354.0
Annual Total Wages                                   0.00               9.0
Annual Average Weekly Wage                     1687166.00            1960.0
Annual Average Pay                                   0.00               9.0
Employment Location Quotient Relative to U.S.     2833.84            3142.0
Total Wage Location Quotient Relative to U.S.     2811.42            3142.0

Count of Non-NaN have to be 3142 (same number of Counties), so here we have an indicator of some issue that is in the database. Of course, is related with dtype, there are object type of data, and have to be number type.

#Try to fix> Make a COPY, convert into numbers selected columns

In [315]:
# Create a copy of businesspriv called final
final = businesspriv.copy()

# List of columns to convert to numeric
cols_to_numeric = [
    'BA2023',
    'Annual Average Establishment Count',
    'Annual Average Employment',
    'Annual Total Wages',
    'Annual Average Weekly Wage',
    'Annual Average Pay',
    'Employment Location Quotient Relative to U.S.',
    'Total Wage Location Quotient Relative to U.S.'
]

# Convert selected columns to numeric
for col in cols_to_numeric:
    final[col] = pd.to_numeric(final[col], errors='coerce')

# Review data types
final.dtypes


State                                              object
County_x                                           object
County Code                                        object
BA2023                                            float64
Area Type                                          object
St Name                                            object
County_y                                           object
Ownership                                          object
Industry                                           object
Annual Average Establishment Count                float64
Annual Average Employment                         float64
Annual Total Wages                                float64
Annual Average Weekly Wage                        float64
Annual Average Pay                                float64
Employment Location Quotient Relative to U.S.     float64
Total Wage Location Quotient Relative to U.S.     float64
_merge                                           category
dtype: object

In [316]:
final

State           County_x County Code  BA2023 Area Type  St Name  \
0       AL     Autauga County       01001   703.0    County  Alabama   
1       AL     Baldwin County       01003  3855.0    County  Alabama   
2       AL     Barbour County       01005   421.0    County  Alabama   
3       AL        Bibb County       01007   173.0    County  Alabama   
4       AL      Blount County       01009   513.0    County  Alabama   
...    ...                ...         ...     ...       ...      ...   
3151    WY  Sweetwater County       56037   839.0    County  Wyoming   
3152    WY       Teton County       56039  1374.0    County  Wyoming   
3153    WY       Uinta County       56041   290.0    County  Wyoming   
3154    WY    Washakie County       56043   112.0    County  Wyoming   
3155    WY      Weston County       56045    74.0    County  Wyoming   

                        County_y Ownership                  Industry  \
0        Autauga County, Alabama   Private  10 Total, all industries   
1        Baldwin County, Alabama   Private  10 Total, all industries   
2        Barbour County, Alabama   Private  10 Total, all industries   
3           Bibb County, Alabama   Private  10 Total, all industries   
4         Blount County, Alabama   Private  10 Total, all industries   
...                          ...       ...                       ...   
3151  Sweetwater County, Wyoming   Private  10 Total, all industries   
3152       Teton County, Wyoming   Private  10 Total, all industries   
3153       Uinta County, Wyoming   Private  10 Total, all industries   
3154    Washakie County, Wyoming   Private  10 Total, all industries   
3155      Weston County, Wyoming   Private  10 Total, all industries   

      Annual Average Establishment Count  Annual Average Employment  \
0                                    NaN                        NaN   
1                                    NaN                        NaN   
2                                  533.0                        NaN   
3                                  380.0                        NaN   
4                                  867.0                        NaN   
...                                  ...                        ...   
3151                                 NaN                        NaN   
3152                                 NaN                        NaN   
3153                               803.0                        NaN   
3154                               404.0                        NaN   
3155                               244.0                        NaN   

      Annual Total Wages  Annual Average Weekly Wage  Annual Average Pay  \
0                    NaN                       936.0                 NaN   
1                    NaN                       929.0                 NaN   
2                    NaN                       816.0                 NaN   
3                    NaN                         NaN                 NaN   
4                    NaN                       839.0                 NaN   
...                  ...                         ...                 ...   
3151                 NaN                         NaN                 NaN   
3152                 NaN                         NaN                 NaN   
3153                 NaN                       958.0                 NaN   
3154                 NaN                       930.0                 NaN   
3155                 NaN                       967.0                 NaN   

      Employment Location Quotient Relative to U.S.  \
0                                              0.92   
1                                              1.01   
2                                              0.94   
3                                              0.85   
4                                              0.89   
...                                             ...   
3151                                           0.94   
3152                                           1.03   
3153          

In [317]:
# List of columns to check
columns_to_check = [
    'Annual Average Establishment Count',
    'Annual Average Employment',
    'Annual Total Wages',
    'Annual Average Weekly Wage',
    'Annual Average Pay'
]

# Count NaN values in each selected column
nan_counts = final[columns_to_check].isna().sum()

# Display the results
print(nan_counts)


Annual Average Establishment Count    1160
Annual Average Employment             2788
Annual Total Wages                    3133
Annual Average Weekly Wage            1182
Annual Average Pay                    3133
dtype: int64


In [318]:
# Columns to sum, including BA2023
columns_to_sum = [
    'BA2023',
    'Annual Average Establishment Count',
    'Annual Average Employment',
    'Annual Total Wages',
    'Annual Average Weekly Wage',
    'Annual Average Pay',
    'Employment Location Quotient Relative to U.S.',
    'Total Wage Location Quotient Relative to U.S.'
]

# Sum each column
sums = final[columns_to_sum].apply(pd.to_numeric, errors='coerce').sum()

# Display result
print(sums)

BA2023                                           5402970.00
Annual Average Establishment Count                787588.00
Annual Average Employment                         194470.00
Annual Total Wages                                     0.00
Annual Average Weekly Wage                       1687166.00
Annual Average Pay                                     0.00
Employment Location Quotient Relative to U.S.       2833.84
Total Wage Location Quotient Relative to U.S.       2811.42
dtype: float64


In [319]:
# Check data types of the selected columns before summing
print(final[columns_to_sum].dtypes)


BA2023                                           float64
Annual Average Establishment Count               float64
Annual Average Employment                        float64
Annual Total Wages                               float64
Annual Average Weekly Wage                       float64
Annual Average Pay                               float64
Employment Location Quotient Relative to U.S.    float64
Total Wage Location Quotient Relative to U.S.    float64
dtype: object


Explanation> All columns are now in numeric format (float64). However, when converting from object to number, some data was lost that visually appeared to be numbers but was text in the original database. Even so, the sums before and after the conversion are the same, so no real information was lost in the totals.

#Download final version fixed

In [320]:
#DOWNLOAD THIS LAST VERSION
# A1. Save the file as Excel inside Colab environment
final.to_excel('final.xlsx', index=False)

# 2. Download the file to your computer
from google.colab import files
files.download('final.xlsx')

# B1. Save the file as CSV inside Colab environment
#final.to_csv('final.csv', index=False)

# 2. Download the CSV file to your computer
#from google.colab import files
#files.download('final.csv')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

#Calulations after try to fix

In [321]:
# Filter rows where County Code is '01001' or '01003'
county_filtered = businesspriv[businesspriv['County Code'].isin(['01001', '01003'])]

# Select only the columns you want to see
columns_to_show = [
    'County Code',
    'BA2023',
    'Annual Average Establishment Count',
    'Annual Average Employment',
    'Annual Total Wages',
    'Annual Average Weekly Wage',
    'Annual Average Pay',
    'Employment Location Quotient Relative to U.S.',
    'Total Wage Location Quotient Relative to U.S.'
]

# Display the selected columns for the filtered rows
county_filtered[columns_to_show]



County Code  BA2023 Annual Average Establishment Count  \
0       01001   703.0                              1,011   
1       01003  3855.0                              8,137   

  Annual Average Employment Annual Total Wages Annual Average Weekly Wage  \
0                     9,330        454,329,752                        936   
1                    71,867      3,473,350,164                        929   

  Annual Average Pay  Employment Location Quotient Relative to U.S.  \
0             48,696                                           0.92   
1             48,330                                           1.01   

   Total Wage Location Quotient Relative to U.S.  
0                                           0.89  
1                                           1.00

In [322]:
#Try to sum each columns to see if the numbers works or not. (after convert object into a number each columns)
# Filter rows where County Code is '01001' or '01003'
county_filtered = businesspriv[businesspriv['County Code'].isin(['01001', '01003'])]

# Select only the columns you want to see
columns_to_show = [
    'County Code',
    'BA2023',
    'Annual Average Establishment Count',
    'Annual Average Employment',
    'Annual Total Wages',
    'Annual Average Weekly Wage',
    'Annual Average Pay',
    'Employment Location Quotient Relative to U.S.',
    'Total Wage Location Quotient Relative to U.S.'
]

# Select only those columns
filtered_selected = county_filtered[columns_to_show]

# Calculate the sum only for numeric columns
sums = filtered_selected.drop(columns=['County Code']).apply(pd.to_numeric, errors='coerce').sum()

# Create a new DataFrame row for the totals
sums['County Code'] = 'Total'  # Put 'Total' label in County Code
sums_df = pd.DataFrame([sums])

# Append the sums row at the bottom
final_table = pd.concat([filtered_selected, sums_df], ignore_index=True)

# Display the result
final_table


County Code  BA2023 Annual Average Establishment Count  \
0       01001   703.0                              1,011   
1       01003  3855.0                              8,137   
2       Total  4558.0                                0.0   

  Annual Average Employment Annual Total Wages Annual Average Weekly Wage  \
0                     9,330        454,329,752                        936   
1                    71,867      3,473,350,164                        929   
2                       0.0                0.0                     1865.0   

  Annual Average Pay  Employment Location Quotient Relative to U.S.  \
0             48,696                                           0.92   
1             48,330                                           1.01   
2                0.0                                           1.93   

   Total Wage Location Quotient Relative to U.S.  
0                                           0.89  
1                                           1.00  
2                                           1.89

#Conclusion

When uploading the original Excel files into Python, although the columns in Excel were properly formatted as numbers, Python (through pandas) reads some of these columns as object type instead of float64. This likely happens because even a single empty or irregular cell within a column causes pandas to treat the entire column as text (object) for consistency. As a result, when I later attempt to convert these columns back into numeric format, many values become NaN, leading to data loss. The issue seems to arise during the file import process rather than from the original Excel formatting.